## Loading Dataset

In [1]:
import numpy as np
import pandas as pd

In [2]:
X_fn = "./data/combine_astii_astiii_filter_all_smoothing_norm.npy"
y_fn = "./data/y_astii_astiii_filter_all_new.npy"
patient_fn = "./data/patient_astii_astiii_filter_all_new.npy"
X_train_raw = np.load(X_fn,allow_pickle=True)
y_train_raw = np.load(y_fn,allow_pickle=True)
patient_train_raw = np.load(patient_fn,allow_pickle=True)

classnames=['Acinetobacter', 'Enterobacter','Enterococcus','Escherichia','Klebsiella','Staphylococcus','Streptococcus','Salmonella','Pseudomonas','CoNS']

df_p = pd.DataFrame(X_train_raw)
df_p['Classes'] = y_train_raw
df_p['Patient_ID'] = patient_train_raw 


In [3]:
if not isinstance(X_train_raw, np.ndarray):
    X_train_raw = np.array(X_train_raw, dtype=np.float32)
elif X_train_raw.dtype != np.float32:
    X_train_raw = X_train_raw.astype(np.float32)

### Model Setting

In [4]:
# model
from model import Variant_LeNet,ResNet,RamanNet,ViT
from tqdm import tqdm
import torch
import pandas as pd
import torch.nn as nn
from torch.autograd import Variable
from losses import FocalLoss
from losses import AdaptiveProxyAnchorLoss
from imblearn.metrics import specificity_score
from sklearn.metrics import (
    confusion_matrix,
    accuracy_score,
    precision_score,
    recall_score,
    f1_score,
    auc,
    roc_curve,
)
from pytorchtools import EarlyStopping
import torch.optim as optim
# Plot
from plot import plot_10_genus_ROC_curve, plot_heatmap,plot_tsne_interactive_html
import matplotlib.pyplot as plt

import seaborn as sns
from sklearn.metrics import confusion_matrix
from config import ORDER, STRAINS
import math

# Training setting
n_classes = 10
epochs = 300 
batch_size = 256
num=50


C_total = np.zeros((n_classes, n_classes))
C = np.zeros((n_classes, n_classes))
C_new = np.zeros((n_classes, n_classes))

2025-07-22 20:52:35.072869: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-07-22 20:52:35.072901: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-07-22 20:52:35.073581: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


## LeNet + CE

In [5]:


class Solver:
    def __init__(
        self,
        i,
        dataloaders,
        model,
        model_path,
        device,
        n_classes,
        alpha,
        gpu=-1,
    ):
        self.i = i
        self.dataloaders = dataloaders
        self.device = device
        self.net = model
        self.net = self.net.to(self.device)
        self.n_classes = n_classes
        self.criterion = nn.CrossEntropyLoss(weight=alpha).cuda()
        self.get_num_labeled_class = 2
        self.optimizer = optim.Adam(self.net.parameters(),lr = 0.001)
        self.model_path = model_path


    def iterate(self, epoch, phase):
        if phase == "train":
            self.net.train()
        else:
            self.net.eval()

            
        dataloader = self.dataloaders[phase]
        total_loss = 0
        correct = 0
        total = 0
            
        for batch_idx, (inputs, targets,patients) in enumerate(dataloader):
            inputs, targets,patients = Variable(inputs).to(self.device), Variable(targets.long()).to(self.device), patients
            out,emb= self.net(inputs)
            
            loss = self.criterion(out, targets)
            
            outputs = torch.argmax(out.detach(), dim=1)
            
            if phase == "train":
                self.optimizer.zero_grad()
                loss.backward()
                self.optimizer.step()


            total_loss += loss.item()
            total += targets.size(0)
            correct += outputs.eq(targets).cpu().sum().item()

        total_loss /= (batch_idx + 1)
        total_acc = correct / total

                
        print("\nepoch %d: %s average loss: %.3f | acc: %.2f%% (%d/%d)"
                % (epoch + 1, phase, total_loss, 100.0 * total_acc, correct, total))

        return total_loss,total_acc,out,targets
            

    def train(self, epochs):
        best_loss = float("inf")
        best_acc = 0
        epoch_breaks_classifer = 0
        train_losses = []
        train_acces = [] 
        test_losses = []
        test_acces = [] 


        early_stopping_classifier = EarlyStopping(patience=25, mode='acc', verbose=True)

        for epoch in tqdm(range(epochs)):
            train_loss,train_acc,out,targets =self.iterate(epoch, "train")

            train_losses.append(train_loss)
            train_acces.append(train_acc)

            with torch.no_grad():
                
                test_loss,test_acc,out,targets= self.iterate(epoch, "test")
                    
                test_losses.append(test_loss)
                test_acces.append(test_acc)

                if test_acc > best_acc:
                    best_acc = test_acc
                    checkpoint = {
                        "epoch": epoch,
                         "train_acc":train_acc,
                        "test_acc":test_acc,
                        "test_loss": test_loss,
                        "state_dict": self.net.state_dict(),
                    }
                    print("best test acc found")
                    torch.save(checkpoint, self.model_path)

                early_stopping_classifier(test_acc)

                epoch_breaks_classifer+= 1

                if early_stopping_classifier.early_stop:
                    break  # 停止訓練
        
        if not early_stopping_classifier.early_stop:
            epoch_breaks_classifer = epochs
        

    def test_iterate(self, phase):
        self.net.eval()
        dataloader = self.dataloaders[phase]
        y_pred = []
        y_true = []
        y_pred_prob = []
        
        features_out = []
        features_combine = []
        targets_combine = []
        patient_ids = []
        
        with torch.no_grad():
            for batch_idx, (inputs, targets,patients) in enumerate(dataloader):
                inputs, targets ,patients = Variable(inputs).to('cuda'), Variable(targets.long()).to('cuda'), patients
                out,emb = self.net(inputs)
                outputs = torch.argmax(out.detach(), dim=1)
                outputs_prob = nn.functional.softmax(out.detach(), dim=1)
                y_pred.append(outputs.cpu().numpy())
                y_pred_prob.append(outputs_prob.cpu().numpy())
            
                y_true.append(targets.cpu().numpy())
                
                targets_combine.append(targets.detach().cpu().numpy())
                patient_ids.append(patients)
                features_out.append(out.cpu().numpy())
                features_combine.append(emb.detach().cpu().numpy())

            targets_combine = np.concatenate(targets_combine, axis=0) 
            patient_ids = np.concatenate( patient_ids, axis=0) 
            features_out = np.concatenate(features_out, axis=0)
            features_combine = np.concatenate(features_combine, axis=0)
        
        return (
                np.hstack(y_pred),
                np.hstack(y_true),
                np.vstack(y_pred_prob),
                features_out,
                features_combine,
                targets_combine,
                patient_ids,
            )
    def test(self):
        checkpoint = torch.load(self.model_path)
        epoch = checkpoint["epoch"]
        train_acc = checkpoint["train_acc"]
        test_acc = checkpoint["test_acc"]
        self.net.load_state_dict(checkpoint["state_dict"])
        print("load model at epoch {}, with test acc : {:.3f}".format(epoch+1, test_acc))

        
        _, _ ,_,train_out,train_combined,train_targets,train_patient_ids = self.test_iterate("train")
        y_pred, y_true ,y_pred_prob,out,combined,targets, test_patient_ids,= self.test_iterate("test")
        
        print("total", accuracy_score(y_true, y_pred))
        for i in range(self.n_classes):
            idx = y_true == i
            print("class", i, accuracy_score(y_true[idx], y_pred[idx]))

        return (
            confusion_matrix(y_true, y_pred),
            y_true,
            y_pred,
            accuracy_score(y_true, y_pred),
            y_pred_prob,
            train_acc,
            train_targets,
            targets,
            train_combined,
            combined,
            train_patient_ids,
            test_patient_ids
        )

In [6]:

from datasets_spectrum import spectral_dataloader
from sklearn.model_selection import StratifiedKFold
best_test_accuracy = 0
low_test_accuracy = 1

# metrics
lenet_train_avg_accuracy = []
lenet_avg_accuracy = []
lenet_avg_roc = []

selected_patient_combinations = set()
    
for i in range(num):
    # Initialize empty DataFrames for this iteration's train and test sets
    train_data = pd.DataFrame(columns=df_p.columns)
    test_data = pd.DataFrame(columns=df_p.columns)

    # 當前迭代的訓練集和測試集病患
    max_attempts = 300 # 最大嘗試次數

    for attempt in range(max_attempts):
            
        test_patients = []
        train_patients = []
        
        for class_label, group in df_p.groupby('Classes'):
                # Select one random patient for the test set and the rest for the train set
            num_patients = group['Patient_ID'].nunique()  # Number of unique patients in this class
            test_patient_count = 1
                
            selected_test_patients = group['Patient_ID'].sample(n=test_patient_count, random_state=i).unique()
            test_patients.extend(selected_test_patients)
                
            selected_train_patients = set(group['Patient_ID'].unique()) - set(selected_test_patients)
            train_patients.extend(selected_train_patients)

        patient_combination = (tuple(sorted(train_patients)), tuple(sorted(test_patients)))
                    

        # 檢查組合是否已存在
        if patient_combination not in selected_patient_combinations:
                
            selected_patient_combinations.add(patient_combination)

            test_data = df_p[df_p['Patient_ID'].isin(test_patients)]
            train_data = df_p[df_p['Patient_ID'].isin(train_patients)]
            
            break


    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)
            

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)

    dl_tr = spectral_dataloader(
                            X_train, y_train,patient_train, idxs=None, batch_size=batch_size, shuffle=True
                        )
    dl_test = spectral_dataloader(X_test, y_test,patient_test,idxs=None, batch_size=batch_size, shuffle=False)
    values, counts = np.unique(np.asarray(y_test), return_counts=True)
    dataloaders = {"train": dl_tr, "test": dl_test}

    model = Variant_LeNet(in_channels=1, out_channels=n_classes)

    model_path = f"best_variant_lenet_model_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,train_patient_ids, test_patient_ids= solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    lenet_train_avg_accuracy.append(train_acc)
    lenet_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne_interactive_html(f"variant_lenet_best_test_accuracy_combined_train",f"variant_lenet_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets, train_patient_ids, test_patient_ids,classnames )
      
        plot_heatmap(f"variant_lenet_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne_interactive_html(f"variant_lenet_low_test_accuracy_combined_train",f"variant_lenet_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets,train_patient_ids, test_patient_ids, classnames )
            
        plot_heatmap(f"variant_lenet_low_test_accuracy_heatmap", C,class_names=classnames)
        
    fpr = dict()
    tpr = dict()
    roc_auc = dict()
    for i in range(np.unique(y_true).shape[0]):
        fpr[i], tpr[i], _ = roc_curve(y_test == i, y_pred_prob[:, i])
        roc_auc[i] = auc(fpr[i], tpr[i])
    values = [
            v
            for v in roc_auc.values()
            if isinstance(v, (int, float)) and not math.isnan(v)
    ]
    if values:
        auc_score = sum(values) / len(values)
    lenet_avg_roc.append(auc_score)

    for i in range(n_classes):
        C_new[i] = np.round((C[i] / (counts[i] * num)), 2)

        # Plot confusion matrix
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]
    cm = 100 * C_new / C_new.sum(axis=1)[:, np.newaxis]

        # calculate comfusion matrix
    accuracy = accuracy_score(y_true, y_pred)
    sensitivity = recall_score(y_true, y_pred, average="micro", zero_division=0)
    specificity = cm[1, 1] / (cm[1, 0] + cm[1, 1])
    f1 = f1_score(y_true, y_pred, average="micro", zero_division=0)

    # metrices result
    df = pd.DataFrame(
        {
            "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
            "Recall": [
                    recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
            "Precision": [
                    precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "F1 Score": [
                    f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            }
    )
    print(df.transpose())
    
    plot_10_genus_ROC_curve(f"variant_lenet_{i}_roc_curve", y_true, y_test, y_pred_prob)

    plot_heatmap(f"variant_lenet_{i}_heatmap", cm,class_names=classnames)

plot_heatmap(f"variant_lenet_average_heatmap", C_total,class_names=classnames)


1


  0%|          | 0/300 [00:00<?, ?it/s]


epoch 1: train average loss: 0.734 | acc: 80.44% (20450/25423)


  0%|          | 1/300 [00:00<04:34,  1.09it/s]


epoch 1: test average loss: 1.022 | acc: 65.56% (575/877)
best test acc found

epoch 2: train average loss: 0.428 | acc: 93.38% (23739/25423)


...


epoch 25: test average loss: 1.099 | acc: 76.93% (667/867)
EarlyStopping counter: 24/25 (best: 0.8685)

epoch 26: train average loss: 0.022 | acc: 99.97% (25425/25433)


  8%|▊         | 25/300 [00:19<03:37,  1.27it/s]


epoch 26: test average loss: 0.800 | acc: 78.09% (677/867)
EarlyStopping counter: 25/25 (best: 0.8685)
🔴 Early stopping triggered
load model at epoch 1, with test acc : 0.869



/tmp/ipykernel_3471346/474861799.py:156: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 0.8685121107266436
class 0 1.0
class 1 0.9875
class 2 0.9625
class 3 0.9620253164556962
class 4 0.3
class 5 0.6111111111111112
class 6 0.9333333333333333
class 7 0.9
class 8 1.0
class 9 1.0
                                                             0
Accuracy                                                0.8685
Recall       [1.0, 0.9875, 0.9625, 0.962, 0.3, 0.6111, 0.93...
Specificity  [1.0, 0.9962, 0.9936, 0.9975, 0.9898, 0.9987, ...
Precision    [1.0, 0.9634, 0.939, 0.9744, 0.75, 0.9821, 0.9...
F1 Score     [1.0, 0.9753, 0.9506, 0.9682, 0.4286, 0.7534, ...


In [7]:
print("max test acc:", np.max(lenet_avg_accuracy))
print("min test acc:", np.min(lenet_avg_accuracy))

print("train mean:", np.mean(lenet_train_avg_accuracy))
print("train std:", np.std(lenet_train_avg_accuracy))

    
print("mean:", np.mean(lenet_avg_accuracy))
print("std:", np.std(lenet_avg_accuracy))

    
print("auc mean:", np.mean(lenet_avg_roc))
print("auc std:", np.std(lenet_avg_roc))
    

max test acc: 0.9700805523590333
min test acc: 0.68
train mean: 0.9586426959060129
train std: 0.06479051309729618
mean: 0.8248587048430064
std: 0.08337187630651324
auc mean: 0.9731887801387044
auc std: 0.027007195720342343


## ResNet + CE

In [11]:

from datasets_spectrum import spectral_dataloader
from sklearn.model_selection import StratifiedKFold
best_test_accuracy = 0
low_test_accuracy = 1

resnet_train_avg_accuracy = []
resnet_avg_accuracy = []
resnet_avg_roc = []


selected_patient_combinations = set()
    
for i in range(num):
    # Initialize empty DataFrames for this iteration's train and test sets
    train_data = pd.DataFrame(columns=df_p.columns)
    test_data = pd.DataFrame(columns=df_p.columns)

    # 當前迭代的訓練集和測試集病患
    max_attempts = 300 # 最大嘗試次數

    for attempt in range(max_attempts):
            
        test_patients = []
        train_patients = []


        
        for class_label, group in df_p.groupby('Classes'):
                # Select one random patient for the test set and the rest for the train set
            num_patients = group['Patient_ID'].nunique()  # Number of unique patients in this class
            test_patient_count = 1
                
            selected_test_patients = group['Patient_ID'].sample(n=test_patient_count, random_state=i).unique()
            test_patients.extend(selected_test_patients)
                
            selected_train_patients = set(group['Patient_ID'].unique()) - set(selected_test_patients)
            train_patients.extend(selected_train_patients)

        patient_combination = (tuple(sorted(train_patients)), tuple(sorted(test_patients)))
                    

        # 檢查組合是否已存在
        if patient_combination not in selected_patient_combinations:
                
            selected_patient_combinations.add(patient_combination)

            test_data = df_p[df_p['Patient_ID'].isin(test_patients)]
            train_data = df_p[df_p['Patient_ID'].isin(train_patients)]
            
            break


    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)
            

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)

    dl_tr = spectral_dataloader(
                        X_train, y_train,patient_train, idxs=None, batch_size=batch_size, shuffle=True
                    )
    dl_test = spectral_dataloader(X_test, y_test,patient_test,idxs=None, batch_size=batch_size, shuffle=False)
    values, counts = np.unique(np.asarray(y_test), return_counts=True)
    dataloaders = {"train": dl_tr, "test": dl_test}

    # setting resnet
    layers = 6
    hidden_size = 100
    block_size = 2
    hidden_sizes = [hidden_size] * layers
    num_blocks = [block_size] * layers
    input_dim = 400
    model = ResNet(
                    hidden_sizes,
                    num_blocks,
                    input_dim=input_dim,
                    in_channels=64,
                    n_classes=10,
                )

    model_path = f"best_resnet_model_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,train_patient_ids, test_patient_ids= solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    resnet_train_avg_accuracy.append(train_acc)
    resnet_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne_interactive_html(f"resnet_best_test_accuracy_combined_train",f"resnet_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets, train_patient_ids, test_patient_ids,classnames )
      
        plot_heatmap(f"resnet_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne_interactive_html(f"resnet_low_test_accuracy_combined_train",f"resnet_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets,train_patient_ids, test_patient_ids, classnames )
            
        plot_heatmap(f"resnet_low_test_accuracy_heatmap", C,class_names=classnames)
        
    fpr = dict()
    tpr = dict()
    roc_auc = dict()
    for i in range(np.unique(y_true).shape[0]):
        fpr[i], tpr[i], _ = roc_curve(y_test == i, y_pred_prob[:, i])
        roc_auc[i] = auc(fpr[i], tpr[i])
    values = [
            v
            for v in roc_auc.values()
            if isinstance(v, (int, float)) and not math.isnan(v)
    ]
    if values:
        auc_score = sum(values) / len(values)
    resnet_avg_roc.append(auc_score)

    for i in range(n_classes):
        C_new[i] = np.round((C[i] / (counts[i] * num)), 2)

        # Plot confusion matrix
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]
    cm = 100 * C_new / C_new.sum(axis=1)[:, np.newaxis]

        # calculate comfusion matrix
    accuracy = accuracy_score(y_true, y_pred)
    sensitivity = recall_score(y_true, y_pred, average="micro", zero_division=0)
    specificity = cm[1, 1] / (cm[1, 0] + cm[1, 1])
    f1 = f1_score(y_true, y_pred, average="micro", zero_division=0)

    # metrices result
    df = pd.DataFrame(
        {
            "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
            "Recall": [
                    recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
            "Precision": [
                    precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "F1 Score": [
                    f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            }
    )
    print(df.transpose())

    plot_10_genus_ROC_curve(f"resnet_{i}_roc_curve", y_true, y_test, y_pred_prob)

    plot_heatmap(f"resnet_{i}_heatmap", cm,class_names=classnames)

plot_heatmap(f"resnet_average_heatmap", C_total,class_names=classnames)


1


  0%|          | 0/300 [00:00<?, ?it/s]


epoch 1: train average loss: 1.519 | acc: 71.01% (18052/25423)


  0%|          | 1/300 [00:02<14:15,  2.86s/it]


epoch 1: test average loss: 1.423 | acc: 63.85% (560/877)
best test acc found

epoch 2: train average loss: 0.751 | acc: 88.30% (22449/25423)


...


epoch 35: test average loss: 1.893 | acc: 73.36% (636/867)
EarlyStopping counter: 24/25 (best: 0.9123)

epoch 36: train average loss: 0.011 | acc: 99.59% (25328/25433)


 12%|█▏        | 35/300 [02:00<15:15,  3.46s/it]


epoch 36: test average loss: 1.893 | acc: 78.55% (681/867)
EarlyStopping counter: 25/25 (best: 0.9123)
🔴 Early stopping triggered
load model at epoch 11, with test acc : 0.912



/tmp/ipykernel_3471346/474861799.py:156: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 0.9123414071510957
class 0 0.9871794871794872
class 1 0.9875
class 2 0.9375
class 3 0.9367088607594937
class 4 0.9625
class 5 0.9333333333333333
class 6 0.8888888888888888
class 7 0.55
class 8 1.0
class 9 1.0
                                                             0
Accuracy                                                0.9123
Recall       [0.9872, 0.9875, 0.9375, 0.9367, 0.9625, 0.933...
Specificity  [1.0, 0.9733, 0.9924, 0.9937, 0.9543, 1.0, 1.0...
Precision    [1.0, 0.79, 0.9259, 0.9367, 0.6814, 1.0, 1.0, ...
F1 Score     [0.9935, 0.8778, 0.9317, 0.9367, 0.7979, 0.965...


In [12]:
print("max test acc:", np.max(resnet_avg_accuracy))
print("min test acc:", np.min(resnet_avg_accuracy))

print("train mean:", np.mean(resnet_train_avg_accuracy))
print("train std:", np.std(resnet_train_avg_accuracy))

    
print("mean:", np.mean(resnet_avg_accuracy))
print("std:", np.std(resnet_avg_accuracy))

    
print("auc mean:", np.mean(resnet_avg_roc))
print("auc std:", np.std(resnet_avg_roc))
    

max test acc: 0.9441913439635535
min test acc: 0.6499429874572406
train mean: 0.9534636840580069
train std: 0.061965102468789425
mean: 0.8076883069205182
std: 0.07999943244178792
auc mean: 0.9727012269427141
auc std: 0.024827056817287738


## RamanNet + CE

In [15]:

from datasets_sliding_window import sliding_spectral_dataloader
from sklearn.model_selection import StratifiedKFold
best_test_accuracy = 0
low_test_accuracy = 1

ramannet_train_avg_accuracy = []
ramannet_avg_accuracy = []
ramannet_avg_roc = []


selected_patient_combinations = set()
    
for i in range(num):
    # Initialize empty DataFrames for this iteration's train and test sets
    train_data = pd.DataFrame(columns=df_p.columns)
    test_data = pd.DataFrame(columns=df_p.columns)

    # 當前迭代的訓練集和測試集病患
    max_attempts = 300 # 最大嘗試次數

    for attempt in range(max_attempts):
            
        test_patients = []
        train_patients = []

        if i == 23:
            i =50

        if i == 35:
            i =51

        
        for class_label, group in df_p.groupby('Classes'):
                # Select one random patient for the test set and the rest for the train set
            num_patients = group['Patient_ID'].nunique()  # Number of unique patients in this class
            test_patient_count = 1
                
            selected_test_patients = group['Patient_ID'].sample(n=test_patient_count, random_state=i).unique()
            test_patients.extend(selected_test_patients)
                
            selected_train_patients = set(group['Patient_ID'].unique()) - set(selected_test_patients)
            train_patients.extend(selected_train_patients)

        patient_combination = (tuple(sorted(train_patients)), tuple(sorted(test_patients)))
                    

        # 檢查組合是否已存在
        if patient_combination not in selected_patient_combinations:
                
            selected_patient_combinations.add(patient_combination)

            test_data = df_p[df_p['Patient_ID'].isin(test_patients)]
            train_data = df_p[df_p['Patient_ID'].isin(train_patients)]
            
            break


    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)
            

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)

    dl_tr = sliding_spectral_dataloader(
                        X_train, y_train,patient_train, idxs=None, batch_size=batch_size, shuffle=True
                    )
    dl_test = sliding_spectral_dataloader(X_test, y_test,patient_test,idxs=None, batch_size=batch_size, shuffle=False)
    values, counts = np.unique(np.asarray(y_test), return_counts=True)
    dataloaders = {"train": dl_tr, "test": dl_test}

    model = RamanNet(w_len=50, n_windows=14,n_classes=10)

    model_path = f"best_ramannet_model_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,train_patient_ids, test_patient_ids= solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    ramannet_train_avg_accuracy.append(train_acc)
    ramannet_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne_interactive_html(f"ramannet_best_test_accuracy_combined_train",f"ramannet_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets, train_patient_ids, test_patient_ids,classnames )
      
        plot_heatmap(f"ramannet_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne_interactive_html(f"ramannet_low_test_accuracy_combined_train",f"ramannet_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets,train_patient_ids, test_patient_ids, classnames )
            
        plot_heatmap(f"ramannet_low_test_accuracy_heatmap", C,class_names=classnames)
        
    fpr = dict()
    tpr = dict()
    roc_auc = dict()
    for i in range(np.unique(y_true).shape[0]):
        fpr[i], tpr[i], _ = roc_curve(y_test == i, y_pred_prob[:, i])
        roc_auc[i] = auc(fpr[i], tpr[i])
    values = [
            v
            for v in roc_auc.values()
            if isinstance(v, (int, float)) and not math.isnan(v)
    ]
    if values:
        auc_score = sum(values) / len(values)
    ramannet_avg_roc.append(auc_score)

    for i in range(n_classes):
        C_new[i] = np.round((C[i] / (counts[i] * num)), 2)

        # Plot confusion matrix
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]
    cm = 100 * C_new / C_new.sum(axis=1)[:, np.newaxis]

        # calculate comfusion matrix
    accuracy = accuracy_score(y_true, y_pred)
    sensitivity = recall_score(y_true, y_pred, average="micro", zero_division=0)
    specificity = cm[1, 1] / (cm[1, 0] + cm[1, 1])
    f1 = f1_score(y_true, y_pred, average="micro", zero_division=0)

    # metrices result
    df = pd.DataFrame(
        {
            "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
            "Recall": [
                    recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
            "Precision": [
                    precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "F1 Score": [
                    f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            }
    )
    print(df.transpose())

    plot_10_genus_ROC_curve(f"ramannet_{i}_roc_curve", y_true, y_test, y_pred_prob)

    plot_heatmap(f"ramannet_{i}_heatmap", cm,class_names=classnames)

plot_heatmap(f"ramannet_average_heatmap", C_total,class_names=classnames)


1


  0%|          | 0/300 [00:00<?, ?it/s]


epoch 1: train average loss: 0.818 | acc: 67.94% (17273/25423)


  0%|          | 1/300 [00:01<06:00,  1.21s/it]


epoch 1: test average loss: 0.810 | acc: 67.16% (589/877)
best test acc found

epoch 2: train average loss: 0.439 | acc: 82.09% (20870/25423)


...


epoch 36: test average loss: 0.295 | acc: 87.77% (761/867)
EarlyStopping counter: 24/25 (best: 0.9100)

epoch 37: train average loss: 0.123 | acc: 94.75% (24097/25433)


 12%|█▏        | 36/300 [00:42<05:13,  1.19s/it]


epoch 37: test average loss: 0.245 | acc: 89.50% (776/867)
EarlyStopping counter: 25/25 (best: 0.9100)
🔴 Early stopping triggered
load model at epoch 12, with test acc : 0.910



/tmp/ipykernel_3471346/474861799.py:156: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 0.9100346020761245
class 0 1.0
class 1 0.9875
class 2 0.9625
class 3 0.8734177215189873
class 4 0.95
class 5 0.6555555555555556
class 6 0.9
class 7 0.8
class 8 1.0
class 9 1.0
                                                             0
Accuracy                                                  0.91
Recall       [1.0, 0.9875, 0.9625, 0.8734, 0.95, 0.6556, 0....
Specificity  [1.0, 0.9898, 0.9809, 0.9962, 0.9809, 0.9987, ...
Precision    [1.0, 0.908, 0.837, 0.9583, 0.8352, 0.9833, 1....
F1 Score     [1.0, 0.9461, 0.8953, 0.9139, 0.8889, 0.7867, ...


In [16]:
print("max test acc:", np.max(ramannet_avg_accuracy))
print("min test acc:", np.min(ramannet_avg_accuracy))

print("train mean:", np.mean(ramannet_train_avg_accuracy))
print("train std:", np.std(ramannet_train_avg_accuracy))

    
print("mean:", np.mean(ramannet_avg_accuracy))
print("std:", np.std(ramannet_avg_accuracy))

    
print("auc mean:", np.mean(ramannet_avg_roc))
print("auc std:", np.std(ramannet_avg_roc))

max test acc: 0.9658314350797267
min test acc: 0.5941860465116279
train mean: 0.903111195181632
train std: 0.051131141508886695
mean: 0.8277734913304934
std: 0.08655361880203058
auc mean: 0.9765473997777794
auc std: 0.022551444734079194


## ViT+CE

In [17]:
class Solver:
    def __init__(
        self,
        i,
        dataloaders,
        model,
        model_path,
        device,
        n_classes,
        alpha,
        gpu=-1,
    ):
        self.i = i
        self.dataloaders = dataloaders
        self.device = device
        self.net = model
        self.net = self.net.to(self.device)
        self.n_classes = n_classes
        self.criterion = nn.CrossEntropyLoss(weight=alpha).cuda()
        self.get_num_labeled_class = 2
        self.optimizer = optim.Adam(self.net.parameters(),lr = 0.001)
        self.model_path = model_path


    def iterate(self, epoch, phase):
        if phase == "train":
            self.net.train()
        else:
            self.net.eval()

            
        dataloader = self.dataloaders[phase]
        total_loss = 0
        correct = 0
        total = 0
            
        for batch_idx, (inputs, targets) in enumerate(dataloader):
            inputs, targets = Variable(inputs).to(self.device), Variable(targets.long()).to(self.device)
            out,emb= self.net(inputs)
            
            loss = self.criterion(out, targets)
            
            outputs = torch.argmax(out.detach(), dim=1)
            
            if phase == "train":
                self.optimizer.zero_grad()
                loss.backward()
                self.optimizer.step()


            total_loss += loss.item()
            total += targets.size(0)
            correct += outputs.eq(targets).cpu().sum().item()

        total_loss /= (batch_idx + 1)
        total_acc = correct / total

                
        print("\nepoch %d: %s average loss: %.3f | acc: %.2f%% (%d/%d)"
                % (epoch + 1, phase, total_loss, 100.0 * total_acc, correct, total))

        return total_loss,total_acc,out,targets
            

    def train(self, epochs):
        best_loss = float("inf")
        best_acc = 0
        epoch_breaks_classifer = 0
        train_losses = []
        train_acces = [] 
        test_losses = []
        test_acces = [] 


        early_stopping_classifier = EarlyStopping(patience=25, mode='acc', verbose=True)

        for epoch in tqdm(range(epochs)):
            train_loss,train_acc,out,targets =self.iterate(epoch, "train")

            train_losses.append(train_loss)
            train_acces.append(train_acc)

            with torch.no_grad():
                
                test_loss,test_acc,out,targets= self.iterate(epoch, "test")
                    
                test_losses.append(test_loss)
                test_acces.append(test_acc)

                if test_acc > best_acc:
                    best_acc = test_acc
                    checkpoint = {
                        "epoch": epoch,
                         "train_acc":train_acc,
                        "test_acc":test_acc,
                        "test_loss": test_loss,
                        "state_dict": self.net.state_dict(),
                    }
                    print("best test acc found")
                    torch.save(checkpoint, self.model_path)

                early_stopping_classifier(test_acc)

                epoch_breaks_classifer+= 1

                if early_stopping_classifier.early_stop:
                    break  # 停止訓練
        
        if not early_stopping_classifier.early_stop:
            epoch_breaks_classifer = epochs
        

    def test_iterate(self, phase):
        self.net.eval()
        dataloader = self.dataloaders[phase]
        y_pred = []
        y_true = []
        y_pred_prob = []
        
        features_out = []
        features_combine = []
        targets_combine = []
        patient_ids = []
        
        with torch.no_grad():
            for batch_idx, (inputs, targets) in enumerate(dataloader):
                inputs, targets = Variable(inputs).to('cuda'), Variable(targets.long()).to('cuda')
                out,emb = self.net(inputs)
                outputs = torch.argmax(out.detach(), dim=1)
                outputs_prob = nn.functional.softmax(out.detach(), dim=1)
                y_pred.append(outputs.cpu().numpy())
                y_pred_prob.append(outputs_prob.cpu().numpy())
            
                y_true.append(targets.cpu().numpy())
                
                targets_combine.append(targets.detach().cpu().numpy())
                features_out.append(out.cpu().numpy())
                features_combine.append(emb.detach().cpu().numpy())

            targets_combine = np.concatenate(targets_combine, axis=0) 
            features_out = np.concatenate(features_out, axis=0)
            features_combine = np.concatenate(features_combine, axis=0)
        
        return (
                np.hstack(y_pred),
                np.hstack(y_true),
                np.vstack(y_pred_prob),
                features_out,
                features_combine,
                targets_combine,
            )
    def test(self):
        checkpoint = torch.load(self.model_path)
        epoch = checkpoint["epoch"]
        train_acc = checkpoint["train_acc"]
        test_acc = checkpoint["test_acc"]
        self.net.load_state_dict(checkpoint["state_dict"])
        print("load model at epoch {}, with test acc : {:.3f}".format(epoch+1, test_acc))

        
        _, _ ,_,train_out,train_combined,train_targets = self.test_iterate("train")
        y_pred, y_true ,y_pred_prob,out,combined,targets= self.test_iterate("test")
        
        print("total", accuracy_score(y_true, y_pred))
        for i in range(self.n_classes):
            idx = y_true == i
            print("class", i, accuracy_score(y_true[idx], y_pred[idx]))

        return (
            confusion_matrix(y_true, y_pred),
            y_true,
            y_pred,
            accuracy_score(y_true, y_pred),
            y_pred_prob,
            train_acc,
            train_targets,
            targets,
            train_combined,
            combined,
        )

In [18]:
from sklearn.model_selection import StratifiedKFold
import torch.utils.data as Data
from plot import plot_tsne
best_test_accuracy = 0
low_test_accuracy = 1

ViT_train_avg_accuracy = []
ViT_avg_accuracy = []
ViT_avg_roc = []


selected_patient_combinations = set()
    
for i in range(num):

    if i == 23:
        i =50

    if i == 35:
        i =51
    train_data = pd.DataFrame(columns=df_p.columns)
    test_data = pd.DataFrame(columns=df_p.columns)

         # 當前迭代的訓練集和測試集病患
    max_attempts = 100  # 最大嘗試次數
    combination_found = False  # 記錄是否找到新組合

    for attempt in range(max_attempts):
        test_patients = []
        train_patients = []

        for class_label, group in df_p.groupby('Classes'):
                # Select one random patient for the test set and the rest for the train set
            num_patients = group['Patient_ID'].nunique()  # Number of unique patients in this class
            test_patient_count = 1
                
            selected_test_patients = group['Patient_ID'].sample(n=test_patient_count, random_state=i).unique()
            test_patients.extend(selected_test_patients)
                
            selected_train_patients = set(group['Patient_ID'].unique()) - set(selected_test_patients)
            train_patients.extend(selected_train_patients)

        patient_combination = (tuple(sorted(train_patients)), tuple(sorted(test_patients)))

        # 檢查組合是否已存在
        if patient_combination not in selected_patient_combinations:
            selected_patient_combinations.add(patient_combination)

            test_data = df_p[df_p['Patient_ID'].isin(test_patients)]
            train_data = df_p[df_p['Patient_ID'].isin(train_patients)]

            combination_found = True
            break


    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)
    
    # Set up dataloaders
    X_train = torch.from_numpy(X_train.astype(np.float32))
    y_train = torch.from_numpy(y_train.astype(np.longlong))


    if isinstance(X_test, np.ndarray):
        X_test = torch.from_numpy(X_test).float()
    else:
        X_test = X_test.float()  # 如果 X_test 已經是張量

    if isinstance(y_test, np.ndarray):
        y_test = torch.from_numpy(y_test).long()
    else:
        y_test = y_test.long()  # 如果 y_test 已經是張量


    dataset_tr = Data.TensorDataset(X_train, y_train)
    dl_tr = Data.DataLoader(dataset_tr, batch_size=batch_size, shuffle = True)
        
        
    dataset_test = Data.TensorDataset(X_test, y_test)
    dl_test = Data.DataLoader(dataset_test, batch_size=batch_size, shuffle = False)
    
    values, counts = np.unique(np.asarray(y_test), return_counts=True)

    dataloaders = {"train": dl_tr, "test": dl_test}

    model = ViT(image_size = (1,400), patch_size = (1, 16), num_classes = n_classes, channels = 1, dim = 64, depth = 3, heads = 6, mlp_dim = 128, dropout = 0.1, emb_dropout = 0.1)

    model_path = f"best_ViT_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined = solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    ViT_train_avg_accuracy.append(train_acc)
    ViT_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne(f"ViT_best_test_accuracy_combined_train",f"ViT_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets,classnames )
      
        plot_heatmap(f"ViT_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne(f"ViT_low_test_accuracy_combined_train",f"ViT_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets, classnames )
            
        plot_heatmap(f"ViT_low_test_accuracy_heatmap", C,class_names=classnames)
        
        
    fpr = dict()
    tpr = dict()
    roc_auc = dict()
    for i in range(np.unique(y_true).shape[0]):
        fpr[i], tpr[i], _ = roc_curve(y_test == i, y_pred_prob[:, i])
        roc_auc[i] = auc(fpr[i], tpr[i])
    values = [
            v
            for v in roc_auc.values()
            if isinstance(v, (int, float)) and not math.isnan(v)
    ]
    if values:
        auc_score = sum(values) / len(values)
    ViT_avg_roc.append(auc_score)

    for i in range(n_classes):
        C_new[i] = np.round((C[i] / (counts[i] * num)), 2)

        # Plot confusion matrix
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]
    cm = 100 * C_new / C_new.sum(axis=1)[:, np.newaxis]

        # calculate comfusion matrix
    accuracy = accuracy_score(y_true, y_pred)
    sensitivity = recall_score(y_true, y_pred, average="micro", zero_division=0)
    specificity = cm[1, 1] / (cm[1, 0] + cm[1, 1])
    f1 = f1_score(y_true, y_pred, average="micro", zero_division=0)

    # metrices result
    df = pd.DataFrame(
        {
            "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
            "Recall": [
                    recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
            "Precision": [
                    precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "F1 Score": [
                    f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            }
    )
    print(df.transpose())

    plot_10_genus_ROC_curve(f"ViT_{i}_roc_curve", y_true, y_test, y_pred_prob)

    plot_heatmap(f"ViT_{i}_heatmap", cm,class_names=classnames)

plot_heatmap(f"ViT_average_heatmap", C_total,class_names=classnames)


1


  0%|          | 1/300 [00:00<04:25,  1.13it/s]


epoch 1: train average loss: 1.858 | acc: 41.42% (10530/25423)

epoch 1: test average loss: 1.401 | acc: 53.25% (467/877)
best test acc found


  1%|          | 2/300 [00:01<04:16,  1.16it/s]


epoch 2: train average loss: 1.154 | acc: 65.39% (16625/25423)

epoch 2: test average loss: 1.047 | acc: 66.93% (587/877)
best test acc found


...


epoch 50: train average loss: 0.135 | acc: 93.91% (23884/25433)

epoch 50: test average loss: 0.838 | acc: 82.24% (713/867)
EarlyStopping counter: 24/25 (best: 0.8800)


 17%|█▋        | 50/300 [00:43<03:39,  1.14it/s]


epoch 51: train average loss: 0.125 | acc: 94.38% (24004/25433)

epoch 51: test average loss: 1.073 | acc: 79.47% (689/867)
EarlyStopping counter: 25/25 (best: 0.8800)
🔴 Early stopping triggered
load model at epoch 26, with test acc : 0.880



/tmp/ipykernel_3471346/960659495.py:153: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 0.8800461361014994
class 0 0.9615384615384616
class 1 0.975
class 2 0.975
class 3 0.9113924050632911
class 4 0.8125
class 5 0.9
class 6 0.7555555555555555
class 7 0.59
class 8 1.0
class 9 0.9666666666666667
                                                             0
Accuracy                                                  0.88
Recall       [0.9615, 0.975, 0.975, 0.9114, 0.8125, 0.9, 0....
Specificity  [1.0, 0.967, 0.9898, 0.9848, 0.9657, 0.9961, 0...
Precision    [1.0, 0.75, 0.907, 0.8571, 0.7065, 0.9643, 0.9...
F1 Score     [0.9804, 0.8478, 0.9398, 0.8834, 0.7558, 0.931...


In [19]:
print("max test acc:", np.max(ViT_avg_accuracy))
print("min test acc:", np.min(ViT_avg_accuracy))

print("train mean:", np.mean(ViT_train_avg_accuracy))
print("train std:", np.std(ViT_train_avg_accuracy))

    
print("mean:", np.mean(ViT_avg_accuracy))
print("std:", np.std(ViT_avg_accuracy))

    
print("auc mean:", np.mean(ViT_avg_roc))
print("auc std:", np.std(ViT_avg_roc))

max test acc: 0.9612756264236902
min test acc: 0.668918918918919
train mean: 0.8635353695897586
train std: 0.0928614845328893
mean: 0.8152588206272509
std: 0.06977758826662349
auc mean: 0.9768870170946943
auc std: 0.01899826899594362


## LeNet + MAPA + Focal

In [20]:
class Solver:
    def __init__(
        self,
        i,
        dataloaders,
        model,
        model_path,
        device,
        n_classes,
        alpha,
        gpu=-1,
    ):
        self.i = i
        self.dataloaders = dataloaders
        self.device = device
        self.net = model
        self.net = self.net.to(self.device)
        self.n_classes = n_classes
        self.criterion_proxy =AdaptiveProxyAnchorLoss(nb_classes=n_classes, sz_embed=256, mrg=0.5, alpha=32,\
                                             nb_proxies=1, scale_margin=1).cuda()
        self.criterion = FocalLoss(alpha=alpha, gamma=2).cuda()
        self.get_num_labeled_class = 2
        self.param_groups = [
            {'params': list(set(model.parameters()).difference(set(model.embedding.parameters())))},
            {'params': model.embedding.parameters() , 'lr':float(0.001) * 1},
            {'params': self.criterion_proxy.mrg,'lr':float(0.001) },
            {'params': self.criterion_proxy.proxies, 'lr':float(0.001) * 10}
        ]
        self.optimizer =torch.optim.AdamW(self.param_groups, lr=0.001, weight_decay = 0.001)
        self.model_path = model_path


    def iterate(self, epoch, phase):
        if phase == "train":
            self.net.train()
        else:
            self.net.eval()

            
        dataloader = self.dataloaders[phase]
        total_loss = 0
        correct = 0
        total = 0
        total_proxy_loss = 0
        total_crossentropy_loss = 0
            
        for batch_idx, (inputs, targets,patients) in enumerate(dataloader):
            inputs, targets,patients = Variable(inputs).to(self.device), Variable(targets.long()).to(self.device), patients
            #print(inputs.shape)
            out,emb= self.net(inputs)
            
            loss1 = self.criterion(out, targets)
            loss2 = self.criterion_proxy(emb, targets)
            loss = loss1 + 0.5 * loss2
            outputs = torch.argmax(out.detach(), dim=1)
            
            if phase == "train":
                self.optimizer.zero_grad()
                loss.backward()
                self.optimizer.step()
                torch.nn.utils.clip_grad_value_(self.net.parameters(), 10)
                torch.nn.utils.clip_grad_value_(self.criterion_proxy.parameters(), 10)


            total_loss += loss.item()
            total_proxy_loss += loss2.item()
            total_crossentropy_loss += loss1.item()
            total += targets.size(0)
            correct += outputs.eq(targets).cpu().sum().item()

        total_loss /= (batch_idx + 1)
        total_acc = correct / total

                
        print("\nepoch %d: %s average loss: %.3f | acc: %.2f%% (%d/%d)"
                % (epoch + 1, phase, total_loss, 100.0 * total_acc, correct, total))

        return total_loss,total_acc,out,targets
            

    def train(self, epochs):
        best_loss = float("inf")
        best_acc = 0
        epoch_breaks_classifer = 0
        train_losses = []
        train_acces = [] 
        test_losses = []
        test_acces = [] 

        self.scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(self.optimizer, T_max=60)

        early_stopping_classifier = EarlyStopping(patience=25, mode='acc', verbose=True)

        for epoch in tqdm(range(epochs)):
            train_loss,train_acc,out,targets =self.iterate(epoch, "train")

            train_losses.append(train_loss)
            train_acces.append(train_acc)

            with torch.no_grad():
                
                test_loss,test_acc,out,targets= self.iterate(epoch, "test")
                    
                test_losses.append(test_loss)
                test_acces.append(test_acc)

                if test_acc > best_acc:
                    best_acc = test_acc
                    checkpoint = {
                        "epoch": epoch,
                         "train_acc":train_acc,
                        "test_acc":test_acc,
                        "test_loss": test_loss,
                        "state_dict": self.net.state_dict(),
                    }
                    print("best test acc found")
                    torch.save(checkpoint, self.model_path)
                
                self.scheduler.step()

                early_stopping_classifier(test_acc)

                epoch_breaks_classifer+= 1

                if early_stopping_classifier.early_stop:
                    break  # 停止訓練
        
        if not early_stopping_classifier.early_stop:
            epoch_breaks_classifer = epochs
        

    def test_iterate(self, phase):
        self.net.eval()
        dataloader = self.dataloaders[phase]
        y_pred = []
        y_true = []
        y_pred_prob = []
        
        features_out = []
        features_combine = []
        targets_combine = []
        patient_ids = []
        
        with torch.no_grad():
            for batch_idx, (inputs, targets,patients) in enumerate(dataloader):
                inputs, targets ,patients = Variable(inputs).to('cuda'), Variable(targets.long()).to('cuda'), patients
                out,emb = self.net(inputs)
                outputs = torch.argmax(out.detach(), dim=1)
                outputs_prob = nn.functional.softmax(out.detach(), dim=1)
                y_pred.append(outputs.cpu().numpy())
                y_pred_prob.append(outputs_prob.cpu().numpy())
            
                y_true.append(targets.cpu().numpy())
                
                targets_combine.append(targets.detach().cpu().numpy())
                patient_ids.append(patients)
                features_out.append(out.cpu().numpy())
                features_combine.append(emb.detach().cpu().numpy())

            targets_combine = np.concatenate(targets_combine, axis=0) 
            patient_ids = np.concatenate( patient_ids, axis=0) 
            features_out = np.concatenate(features_out, axis=0)
            features_combine = np.concatenate(features_combine, axis=0)
        
        return (
                np.hstack(y_pred),
                np.hstack(y_true),
                np.vstack(y_pred_prob),
                features_out,
                features_combine,
                targets_combine,
                patient_ids,
            )
    def test(self):
        checkpoint = torch.load(self.model_path)
        epoch = checkpoint["epoch"]
        train_acc = checkpoint["train_acc"]
        test_acc = checkpoint["test_acc"]
        self.net.load_state_dict(checkpoint["state_dict"])
        print("load model at epoch {}, with test acc : {:.3f}".format(epoch+1, test_acc))

        
        _, _ ,_,train_out,train_combined,train_targets,train_patient_ids = self.test_iterate("train")
        y_pred, y_true ,y_pred_prob,out,combined,targets, test_patient_ids,= self.test_iterate("test")
        
        print("total", accuracy_score(y_true, y_pred))
        for i in range(self.n_classes):
            idx = y_true == i
            print("class", i, accuracy_score(y_true[idx], y_pred[idx]))

        return (
            confusion_matrix(y_true, y_pred),
            y_true,
            y_pred,
            accuracy_score(y_true, y_pred),
            y_pred_prob,
            train_acc,
            train_targets,
            targets,
            train_combined,
            combined,
            train_patient_ids,
            test_patient_ids
        )

In [21]:

from datasets_spectrum import spectral_dataloader
from sklearn.model_selection import StratifiedKFold
best_test_accuracy = 0
low_test_accuracy = 1

# metrics
lenet_mapa_focal_train_avg_accuracy = []
lenet_mapa_focal_avg_accuracy = []
lenet_mapa_focal_avg_roc = []

selected_patient_combinations = set()
    
for i in range(num):
    # Initialize empty DataFrames for this iteration's train and test sets
    train_data = pd.DataFrame(columns=df_p.columns)
    test_data = pd.DataFrame(columns=df_p.columns)

    # 當前迭代的訓練集和測試集病患
    max_attempts = 300 # 最大嘗試次數

    for attempt in range(max_attempts):
            
        test_patients = []
        train_patients = []

        if i == 23:
            i =50

        if i == 35:
            i =51

        
        for class_label, group in df_p.groupby('Classes'):
                # Select one random patient for the test set and the rest for the train set
            num_patients = group['Patient_ID'].nunique()  # Number of unique patients in this class
            test_patient_count = 1
                
            selected_test_patients = group['Patient_ID'].sample(n=test_patient_count, random_state=i).unique()
            test_patients.extend(selected_test_patients)
                
            selected_train_patients = set(group['Patient_ID'].unique()) - set(selected_test_patients)
            train_patients.extend(selected_train_patients)

        patient_combination = (tuple(sorted(train_patients)), tuple(sorted(test_patients)))
                    

        # 檢查組合是否已存在
        if patient_combination not in selected_patient_combinations:
                
            selected_patient_combinations.add(patient_combination)

            test_data = df_p[df_p['Patient_ID'].isin(test_patients)]
            train_data = df_p[df_p['Patient_ID'].isin(train_patients)]
            
            break


    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)
            

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)

    dl_tr = spectral_dataloader(
                        X_train, y_train,patient_train, idxs=None, batch_size=batch_size, shuffle=True
                    )
    dl_test = spectral_dataloader(X_test, y_test,patient_test,idxs=None, batch_size=batch_size, shuffle=False)
    values, counts = np.unique(np.asarray(y_test), return_counts=True)
    dataloaders = {"train": dl_tr, "test": dl_test}

    model = Variant_LeNet(in_channels=1, out_channels=n_classes)

    model_path = f"best_variant_lenet_mapa_focal_model_{i}.pth"

    class_counts = np.bincount(y_train)
    num_classes = len(class_counts)
    total_samples = len(y_train)

    class_weights = []
    for count in class_counts:
        weight = 1 / (count / total_samples)
        class_weights.append(weight)
    class_weights = torch.FloatTensor(class_weights)
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,train_patient_ids, test_patient_ids= solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    lenet_mapa_focal_train_avg_accuracy.append(train_acc)
    lenet_mapa_focal_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne_interactive_html(f"lenet_mapa_focal_best_test_accuracy_combined_train",f"lenet_mapa_focal_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets, train_patient_ids, test_patient_ids,classnames )
      
        plot_heatmap(f"lenet_mapa_focal_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne_interactive_html(f"lenet_mapa_focal_low_test_accuracy_combined_train",f"lenet_mapa_focal_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets,train_patient_ids, test_patient_ids, classnames )
            
        plot_heatmap(f"lenet_mapa_focal_low_test_accuracy_heatmap", C,class_names=classnames)
        
    fpr = dict()
    tpr = dict()
    roc_auc = dict()
    for i in range(np.unique(y_true).shape[0]):
        fpr[i], tpr[i], _ = roc_curve(y_test == i, y_pred_prob[:, i])
        roc_auc[i] = auc(fpr[i], tpr[i])
    values = [
            v
            for v in roc_auc.values()
            if isinstance(v, (int, float)) and not math.isnan(v)
    ]
    if values:
        auc_score = sum(values) / len(values)
    lenet_mapa_focal_avg_roc.append(auc_score)

    for i in range(n_classes):
        C_new[i] = np.round((C[i] / (counts[i] * num)), 2)

        # Plot confusion matrix
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]
    cm = 100 * C_new / C_new.sum(axis=1)[:, np.newaxis]

        # calculate comfusion matrix
    accuracy = accuracy_score(y_true, y_pred)
    sensitivity = recall_score(y_true, y_pred, average="micro", zero_division=0)
    specificity = cm[1, 1] / (cm[1, 0] + cm[1, 1])
    f1 = f1_score(y_true, y_pred, average="micro", zero_division=0)

    # metrices result
    df = pd.DataFrame(
        {
            "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
            "Recall": [
                    recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
            "Precision": [
                    precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "F1 Score": [
                    f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            }
    )
    print(df.transpose())

    plot_10_genus_ROC_curve(f"lenet_mapa_focal_{i}_roc_curve", y_true, y_test, y_pred_prob)

    plot_heatmap(f"lenet_mapa_focal_{i}_heatmap", cm,class_names=classnames)

plot_heatmap(f"lenet_mapa_focal_average_heatmap", C_total,class_names=classnames)


1


  0%|          | 0/300 [00:00<?, ?it/s]


epoch 1: train average loss: 22.282 | acc: 78.64% (19992/25423)


  0%|          | 1/300 [00:01<06:19,  1.27s/it]


epoch 1: test average loss: 27.975 | acc: 64.65% (567/877)
best test acc found

epoch 2: train average loss: 15.594 | acc: 92.29% (23463/25423)


...


epoch 30: test average loss: 28.509 | acc: 80.51% (698/867)
EarlyStopping counter: 24/25 (best: 0.8616)

epoch 31: train average loss: 5.530 | acc: 100.00% (25432/25433)


 10%|█         | 30/300 [00:37<05:37,  1.25s/it]


epoch 31: test average loss: 41.062 | acc: 77.16% (669/867)
EarlyStopping counter: 25/25 (best: 0.8616)
🔴 Early stopping triggered
load model at epoch 6, with test acc : 0.862



/tmp/ipykernel_3471346/3696667578.py:175: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 0.8615916955017301
class 0 1.0
class 1 1.0
class 2 0.9625
class 3 0.810126582278481
class 4 0.825
class 5 0.9111111111111111
class 6 0.7111111111111111
class 7 0.48
class 8 1.0
class 9 0.9777777777777777
                                                             0
Accuracy                                                0.8616
Recall       [1.0, 1.0, 0.9625, 0.8101, 0.825, 0.9111, 0.71...
Specificity  [1.0, 0.9784, 0.953, 0.9962, 0.9504, 0.9961, 1...
Precision    [1.0, 0.8247, 0.6754, 0.9552, 0.6286, 0.9647, ...
F1 Score     [1.0, 0.904, 0.7938, 0.8767, 0.7135, 0.9371, 0...


In [22]:
print("max test acc:", np.max(lenet_mapa_focal_avg_accuracy))
print("min test acc:", np.min(lenet_mapa_focal_avg_accuracy))

print("train mean:", np.mean(lenet_mapa_focal_train_avg_accuracy))
print("train std:", np.std(lenet_mapa_focal_train_avg_accuracy))

    
print("mean:", np.mean(lenet_mapa_focal_avg_accuracy))
print("std:", np.std(lenet_mapa_focal_avg_accuracy))

    
print("auc mean:", np.mean(lenet_mapa_focal_avg_roc))
print("auc std:", np.std(lenet_mapa_focal_avg_roc))

max test acc: 0.9585730724971231
min test acc: 0.6598984771573604
train mean: 0.9523873954251159
train std: 0.06866968596603476
mean: 0.8272988403416548
std: 0.08153161532444532
auc mean: 0.9731505449341493
auc std: 0.025672220086388586


In [23]:
import numpy as np

# 將模型名稱與對應數據組成字典，便於迴圈處理
models = {
    "LeNet + MAPA + Focal": lenet_mapa_focal_avg_accuracy,
    "RamanNet + CE": ramannet_avg_accuracy,
    "LeNet + CE": lenet_avg_accuracy,
    "ResNet + CE": resnet_avg_accuracy,
    "ViT + CE": ViT_avg_accuracy
}

# 輸出結果
print("Model Comparison (Mean ± Std):")
for name, acc in models.items():
    mean_acc = np.mean(acc)
    std_acc = np.std(acc)
    print(f"{name:<20}: {mean_acc:.4f} ± {std_acc:.4f}")


Model Comparison (Mean ± Std):
LeNet + MAPA + Focal: 0.8273 ± 0.0815
RamanNet + CE       : 0.8278 ± 0.0866
LeNet + CE          : 0.8249 ± 0.0834
ResNet + CE         : 0.8077 ± 0.0800
ViT + CE            : 0.8153 ± 0.0698
